#Predicting sentiment from product reviews

#Fire up GraphLab Create

In [2]:
import graphlab

#Read some product review data

Loading reviews for a set of baby products. 

In [3]:
products = graphlab.SFrame('data/amazon_baby.gl/')

[INFO] 1450380402 : INFO:     (initialize_globals_from_environment:282): Setting configuration variable GRAPHLAB_FILEIO_ALTERNATIVE_SSL_CERT_FILE to /Users/bbalaji-2012/.graphlab/anaconda/lib/python2.7/site-packages/certifi/cacert.pem
1450380402 : INFO:     (initialize_globals_from_environment:282): Setting configuration variable GRAPHLAB_FILEIO_ALTERNATIVE_SSL_CERT_DIR to 
This non-commercial license of GraphLab Create is assigned to bbalaji8@gmail.com and will expire on December 09, 2016. For commercial licensing options, visit https://dato.com/buy/.

[INFO] Start server at: ipc:///tmp/graphlab_server-3059 - Server binary: /Users/bbalaji-2012/.graphlab/anaconda/lib/python2.7/site-packages/graphlab/unity_server - Server log: /tmp/graphlab_server_1450380402.log
[INFO] GraphLab Server Version: 1.7.1


#Let's explore this data together

Data includes the product name, the review text and the rating of the review. 

In [4]:
products.head()

Columns:
	name	str
	review	str
	rating	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|    Planetwise Flannel Wipes   | These flannel wipes are OK... |  3.0   |
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
+-------------------------------+-------------------------------+--------+
[10 rows x 3 columns]

#Build the word count vector for each review

In [5]:
products['word_count'] = graphlab.text_analytics.count_words(products['review'])

In [6]:
products.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|    Planetwise Flannel Wipes   | These flannel wipes are OK... |  3.0   |
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+
|           word_count          |
+-------------------------------+
| {'and': 5, '6': 1, 'stink'... |
| {'and': 3, 'love': 1, 'it'... |
| {'and': 2, 'quilt': 1, 'it... |
| {'ingenious': 1, 'and': 3,... |
| {'and': 2, 'parents!!': 1,... |
| {'and': 2, 'this': 2, 'her... |
| {'shop': 1, 'noble': 1, 'i... |
| {'and': 2, 'all': 1, 'righ... |
| {'and': 1, 'help': 1, 'giv... |
| {'journal.': 1, 'nanny': 1... |
+-------------------------------+
[10 rows x 4 columns]

In [7]:
graphlab.canvas.set_target('ipynb')

In [8]:
products['name'].show()

#Examining the reviews for most-sold product:  'Vulli Sophie the Giraffe Teether'

In [9]:
giraffe_reviews = products[products['name'] == 'Vulli Sophie the Giraffe Teether']

In [10]:
len(giraffe_reviews)

785

In [11]:
giraffe_reviews['rating'].show(view='Categorical')

#Build a sentiment classifier

In [12]:
products['rating'].show(view='Categorical')

##Define what's a positive and a negative sentiment

We will ignore all reviews with rating = 3, since they tend to have a neutral sentiment.  Reviews with a rating of 4 or higher will be considered positive, while the ones with rating of 2 or lower will have a negative sentiment.   

In [13]:
#ignore all 3* reviews
products = products[products['rating'] != 3]

In [14]:
#positive sentiment = 4* or 5* reviews
products['sentiment'] = products['rating'] >=4

In [16]:
products.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	sentiment	int

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
| Baby Tracker&reg; - Daily ... | I love this journal and ou... |  4.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+-----------+
|           word_count          | sentiment |
+-------------------------------+-----------+
| {'and': 3, 'love': 1, 'it'... |     1     |
| {'and': 2, 'quilt': 1, 'it... |     1     |
| {'ingenious': 1, 'and': 3,... |     1     |
| {'and': 2, 'parents!!': 1,... |     1     |
| {'and': 2, 'cute': 1, 'hel... |     1     |
| {'shop': 1, 'be': 1, 'is':... |     1     |
| {'feeding,': 1, 'and': 2, ... |     1     |
| {'and': 1, 'help': 1, 'giv... |     1     |
| {'journal.': 1, 'all': 1, ... |     1     |
| {'all': 1, 'forget': 1, 'j... |     1     |
+-------------------------------+-----------+
[10 rows x 5 columns]

##Let's train the sentiment classifier

In [15]:
train_data,test_data = products.random_split(.8, seed=0)

In [16]:
sentiment_model = graphlab.logistic_classifier.create(train_data,
                                                     target='sentiment',
                                                     features=['word_count'],
                                                     validation_set=test_data)

PROGRESS: Logistic regression:
PROGRESS: --------------------------------------------------------
PROGRESS: Number of examples          : 133448
PROGRESS: Number of classes           : 2
PROGRESS: Number of feature columns   : 1
PROGRESS: Number of unpacked features : 219217
PROGRESS: Number of coefficients    : 219218
PROGRESS: Starting L-BFGS
PROGRESS: --------------------------------------------------------
PROGRESS: +-----------+----------+-----------+--------------+-------------------+---------------------+
PROGRESS: | Iteration | Passes   | Step size | Elapsed Time | Training-accuracy | Validation-accuracy |
PROGRESS: +-----------+----------+-----------+--------------+-------------------+---------------------+
PROGRESS: | 1         | 5        | 0.000002  | 2.353659     | 0.841481          | 0.839989            |
PROGRESS: | 2         | 9        | 3.000000  | 3.616180     | 0.947425          | 0.894877            |
PROGRESS: | 3         | 10       | 3.000000  | 4.083845     | 0.92

#Evaluate the sentiment model

In [17]:
sentiment_model.evaluate(test_data, metric='roc_curve')

{'roc_curve': Columns:
 	threshold	float
 	fpr	float
 	tpr	float
 	p	int
 	n	int
 
 Rows: 100001
 
 Data:
 +-----------+----------------+----------------+-------+------+
 | threshold |      fpr       |      tpr       |   p   |  n   |
 +-----------+----------------+----------------+-------+------+
 |    0.0    |      1.0       |      1.0       | 27976 | 5328 |
 |   1e-05   | 0.909346846847 | 0.998856162425 | 27976 | 5328 |
 |   2e-05   | 0.896021021021 | 0.998748927652 | 27976 | 5328 |
 |   3e-05   | 0.886448948949 | 0.998462968259 | 27976 | 5328 |
 |   4e-05   | 0.879692192192 | 0.998284243637 | 27976 | 5328 |
 |   5e-05   | 0.875187687688 | 0.998212753789 | 27976 | 5328 |
 |   6e-05   | 0.872184684685 | 0.998177008865 | 27976 | 5328 |
 |   7e-05   | 0.868618618619 | 0.998034029168 | 27976 | 5328 |
 |   8e-05   | 0.864677177177 | 0.997998284244 | 27976 | 5328 |
 |   9e-05   | 0.860735735736 | 0.997962539319 | 27976 | 5328 |
 +-----------+----------------+----------------+-------+------

In [18]:
sentiment_model.show(view='Evaluation')

#Applying the learned model to understand sentiment for Giraffe

In [20]:
giraffe_reviews['predicted_sentiment'] = sentiment_model.predict(giraffe_reviews, output_type='probability')

In [21]:
giraffe_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
| Vulli Sophie the Giraffe T... | He likes chewing on all th... |  5.0   |
| Vulli Sophie the Giraffe T... | My son loves this toy and ... |  5.0   |
| Vulli Sophie the Giraffe T... | There really should be a l... |  1.0   |
| Vulli Sophie the Giraffe T... | All the moms in my moms' g... |  5.0   |
| Vulli Sophie the Giraffe T... | I was a little skeptical o... |  5.0   |
| Vulli Sophie the Giraffe T... | I have been reading about ... |  5.0   |
| Vulli Sophie the Giraffe T... | My neice loves her sophie ... |  5.0   |
| Vulli Sophie the Giraffe T... | What a friendly face!  And... |  5.0   |
| Vulli Sophie the Giraffe T... | We got this just for my so... |  5.0   |
| Vulli Sophie the Giraffe T... | My baby seems to like this... |  3.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+---------------------+
|           word_count          | predicted_sentiment |
+-------------------------------+---------------------+
| {'and': 1, 'all': 1, 'beca... |    0.999513023521   |
| {'and': 1, 'right': 1, 'he... |    0.999320678306   |
| {'and': 2, 'all': 1, 'late... |    0.013558811687   |
| {'and': 2, 'one!': 1, 'all... |    0.995769474148   |
| {'and': 3, 'all': 1, 'old'... |    0.662374415673   |
| {'and': 6, 'seven': 1, 'al... |    0.999997148186   |
| {'and': 4, 'drooling,': 1,... |    0.989190989536   |
| {'and': 3, 'chew': 1, "don... |    0.999563518413   |
| {'chew': 2, 'because': 1, ... |    0.970160542725   |
| {'and': 2, 'already': 1, '... |    0.195367644588   |
+-------------------------------+---------------------+
[10 rows x 5 columns]

##Sort the reviews based on the predicted sentiment and explore

In [22]:
giraffe_reviews = giraffe_reviews.sort('predicted_sentiment', ascending=False)

In [24]:
giraffe_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
| Vulli Sophie the Giraffe T... | Sophie, oh Sophie, your ti... |  5.0   |
| Vulli Sophie the Giraffe T... | I'm not sure why Sophie is... |  4.0   |
| Vulli Sophie the Giraffe T... | I'll be honest...I bought ... |  4.0   |
| Vulli Sophie the Giraffe T... | We got this little giraffe... |  5.0   |
| Vulli Sophie the Giraffe T... | As a mother of 16month old... |  5.0   |
| Vulli Sophie the Giraffe T... | Sophie the Giraffe is the ... |  5.0   |
| Vulli Sophie the Giraffe T... | Sophie la giraffe is absol... |  5.0   |
| Vulli Sophie the Giraffe T... | My 5-mos old son took to t... |  5.0   |
| Vulli Sophie the Giraffe T... | My nephews and my four kid... |  5.0   |
| Vulli Sophie the Giraffe T... | Never thought I'd see my s... |  5.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+---------------------+
|           word_count          | predicted_sentiment |
+-------------------------------+---------------------+
| {'giggles': 1, 'all': 1, "... |         1.0         |
| {'peace': 1, 'month': 1, '... |    0.999999999703   |
| {'all': 2, 'pops': 1, 'exi... |    0.999999999392   |
| {'all': 2, "don't": 1, '(l... |    0.99999999919    |
| {'cute': 1, 'all': 1, 'rev... |    0.999999998657   |
| {'just': 2, 'both': 1, 'mo... |    0.999999997108   |
| {'and': 5, 'the': 1, 'all'... |    0.999999995589   |
| {'just': 1, 'shape': 2, 'm... |    0.999999995573   |
| {'and': 4, 'chew': 1, 'all... |    0.999999989527   |
| {'giggles': 1, 'all': 1, '... |    0.999999985069   |
+-------------------------------+---------------------+
[10 rows x 5 columns]

##Most positive reviews for the giraffe

In [25]:
giraffe_reviews[0]['review']

"Sophie, oh Sophie, your time has come. My granddaughter, Violet is 5 months old and starting to teeth. What joy little Sophie brings to Violet. Sophie is made of a very pliable rubber that is sturdy but not tough. It is quite easy for Violet to twist Sophie into unheard of positions to get Sophie into her mouth. The little nose and hooves fit perfectly into small mouths, and the drooling has purpose. The paint on Sophie is food quality.Sophie was born in 1961 in France. The maker had wondered why there was nothing available for babies and made Sophie from the finest rubber, phthalate-free on St Sophie's Day, thus the name was born. Since that time millions of Sophie's populate the world. She is soft and for babies little hands easy to grasp. Violet especially loves the bumpy head and horns of Sophie. Sophie has a long neck that easy to grasp and twist. She has lovely, sizable spots that attract Violet's attention. Sophie has happy little squeaks that bring squeals of delight from Viol

In [26]:
giraffe_reviews[1]['review']

"I'm not sure why Sophie is such a hit with the little ones, but my 7 month old baby girl is one of her adoring fans.  The rubber is softer and more pleasant to handle, and my daughter has enjoyed chewing on her legs and the nubs on her head even before she started teething.  She also loves the squeak that Sophie makes when you squeeze her.  Not sure what it is but if Sophie is amongst a pile of her other toys, my daughter will more often than not reach for Sophie.  And I have the peace of mind of knowing that only edible and safe paints and materials have been used to make Sophie, as opposed to Bright Starts and other baby toys made in China.  Now that the research is out on phthalates and other toxic substances in baby toys, I think it's more important than ever to find good quality toys that are also safe for our babies to handle and put in their mouths.  Sophie is a must-have for every new mom in my opinion.  Even if your kid is one of the few that can take or leave her, it's worth

##Show most negative reviews for giraffe

In [27]:
giraffe_reviews[-1]['review']

"My son (now 2.5) LOVED his Sophie, and I bought one for every baby shower I've gone to. Now, my daughter (6 months) just today nearly choked on it and I will never give it to her again. Had I not been within hearing range it could have been fatal. The strange sound she was making caught my attention and when I went to her and found the front curved leg shoved well down her throat and her face a purply/blue I panicked. I pulled it out and she vomited all over the carpet before screaming her head off. I can't believe how my opinion of this toy has changed from a must-have to a must-not-use. Please don't disregard any of the choking hazard comments, they are not over exaggerated!"

In [28]:
giraffe_reviews[-2]['review']

"This children's toy is nostalgic and very cute. However, there is a distinct rubber smell and a very odd taste, yes I tried it, that my baby did not enjoy. Also, if it is soiled it is extremely difficult to clean as the rubber is a kind of porus material and does not clean well. The final thing is the squeaking device inside which stopped working after the first couple of days. I returned this item feeling I had overpaid for a toy that was defective and did not meet my expectations. Please do not be swayed by the cute packaging and hype surounding it as I was. One more thing, I was given a full refund from Amazon without any problem."

## Select keywords for sentiment analysis

In [19]:
selected_words = ['awesome', 'great', 'fantastic', 'amazing', 'love', 'horrible', 'bad', 'terrible', 'awful', 'wow', 'hate']

In [20]:
selected_words

['awesome',
 'great',
 'fantastic',
 'amazing',
 'love',
 'horrible',
 'bad',
 'terrible',
 'awful',
 'wow',
 'hate']

In [46]:
def awesome_count_old(word_countDct):
    if 'awesome' in word_countDct:
        return word_countDct['awesome']
    else:
        return 0

def awesome_count(word_countDct):
    return (word_countDct['awesome'] if 'awesome' in word_countDct else 0)

In [23]:
giraffe_reviews['word_count'].head()

dtype: dict
Rows: 10
[{'and': 1, 'all': 1, 'because': 1, 'it': 1, 'helped': 1, 'ears!': 1, 'when': 1, 'been': 1, 'parts': 1, 'chewing': 1, 'has': 2, 'head': 1, 'cranky': 1, 'purchase!': 1, 'he': 2, 'on': 1, 'great': 1, 'especially': 1, 'of': 1, 'the': 3, 'teething.': 1, 'likes': 1}, {'and': 1, 'right': 1, 'help': 1, 'just': 1, 'when': 1, 'is': 1, 'in': 1, 'son': 1, 'tooth.': 1, 'water.': 1, 'toy': 1, 'to': 2, 'seems': 1, 'also': 1, 'clean,': 1, 'easy': 1, 'under': 1, 'run': 1, 'very': 1, 'diaper': 1, 'fits': 1, 'him': 1, 'he': 1, 'a': 1, 'great': 1, 'getting': 1, 'this': 1, 'bag.': 1, 'loves': 1, 'the': 2, 'my': 1}, {'and': 2, 'all': 1, 'would': 1, 'latex.': 1, 'being': 1, 'caused': 1, 'mommy': 1, 'allergy': 1, 'idea': 1, 'an': 2, 'packaging': 1, 'someone': 1, 'have': 1, 'in': 2, 'should': 1, 'really': 1, '2011': 1, 'for': 1, 'no': 1, 'allergies': 1, 'box.': 1, 'that': 2, 'teether': 2, 'by': 1, 'anaphylactic': 1, 'was': 2, 'is': 2, 'killed': 1, 'be': 1, 'good': 1, 'on': 2, 'there': 2, 

In [40]:
giraffe_reviews['awesome_count'] = giraffe_reviews['word_count'].apply(awesome_count)

In [42]:
print giraffe_reviews['awesome_count'].head()

[None, None, None, None, None, None, None, None, None, None]


In [41]:
print sum(giraffe_reviews['awesome_count'])

TypeError: unsupported operand type(s) for +: 'int' and 'NoneType'

In [34]:
giraffe_reviews_awesome = giraffe_reviews[giraffe_reviews['awesome_count'] > 0]

In [35]:
print giraffe_reviews_awesome['word_count']

[{'and': 3, 'chew': 1, 'all': 1, 'is': 2, 'back': 1, 'as': 1, 'have': 1, 'rave': 1, 'seem': 1, 'your': 1, 'really': 1, 'what': 1, 'for': 1, 'their': 1, "it's": 1, 'teether': 1, 'worth': 1, 'plastic': 1, 'how': 1, 'does': 1, 'soothes': 1, 'if': 1, 'awesome': 1, 'a': 2, 'to': 1, 'that': 1, 'toy,': 1, 'given': 1, 'but': 1, 'it': 2, 'pricey': 1, 'child': 2, 'it!': 2, 'come': 1, 'moms': 1, 'me': 1, 'loved': 1, 'about': 1, 'several': 1, 'gift': 1, 'this': 2, 'times': 1, 'i': 1, 'the': 1, 'slightly': 1}, {'is': 1, 'it': 2, 'an': 1, 'expensive': 1, 'for': 1, 'cool': 1, 'was': 1, 'worth': 1, 'it.': 1, 'used': 1, 'very': 1, 'but': 1, 'it!': 1, 'son': 1, 'he': 1, 'loved': 1, 'teether.': 2, 'this': 1, 'my': 1, 'months': 1, 'definitely': 1, 'so': 1, 'slightly': 1, 'awesome': 1}, {'all': 1, 'both': 1, 'go': 1, 'still': 1, 'did,': 1, 'price,': 1, 'to': 3, 'does': 1, 'worth': 1, 'not': 1, 'bath': 1, 'dates,': 1, 'like': 1, 'also,': 1, 'where': 1, "isn't": 1, 'chew': 1, 'because': 2, 'another': 1, 'som

In [48]:
tstAwesomeYsDct = {'and' : 3, 'awesome' : 2}
tstAwesomeNoDct = {'and' : 3, 'dummy' : 2}

In [50]:
print tstAwesomeYsDct; print awesome_count(tstAwesomeYsDct)
print tstAwesomeNoDct; print awesome_count(tstAwesomeNoDct)

{'and': 3, 'awesome': 2}
2
{'and': 3, 'dummy': 2}
0


In [55]:
for word in selected_words:
#     print "word: %s" % (word)
    giraffe_reviews[word + '_count'] = giraffe_reviews['word_count'].apply(
        lambda wordCntDct: wordCntDct[word] if word in wordCntDct else 0)
    print "word: %s| sum(count): %d" % (word, sum(giraffe_reviews[word + '_count']))

word: awesome
word: awesome| sum(count): 4
word: great
word: great| sum(count): 152
word: fantastic
word: fantastic| sum(count): 6
word: amazing
word: amazing| sum(count): 2
word: love
word: love| sum(count): 164
word: horrible
word: horrible| sum(count): 4
word: bad
word: bad| sum(count): 15
word: terrible
word: terrible| sum(count): 4
word: awful
word: awful| sum(count): 0
word: wow
word: wow| sum(count): 3
word: hate
word: hate| sum(count): 3


In [56]:
for word in selected_words:
    products[word + '_count'] = products['word_count'].apply(
        lambda wordCntDct: wordCntDct[word] if word in wordCntDct else 0)
    print "word: %s| sum(count): %d" % (word, sum(products[word + '_count']))

word: awesome| sum(count): 2002
word: great| sum(count): 42420
word: fantastic| sum(count): 873
word: amazing| sum(count): 1305
word: love| sum(count): 40277
word: horrible| sum(count): 659
word: bad| sum(count): 3197
word: terrible| sum(count): 673
word: awful| sum(count): 345
word: wow| sum(count): 131
word: hate| sum(count): 1057


In [57]:
print products.head()

+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
| Baby Tracker&reg; - Daily ... | I love this journal and ou... |  4.0   |
+------------------------

In [59]:
[word + '_count' for word in selected_words]

['awesome_count',
 'great_count',
 'fantastic_count',
 'amazing_count',
 'love_count',
 'horrible_count',
 'bad_count',
 'terrible_count',
 'awful_count',
 'wow_count',
 'hate_count']

In [61]:
train_data,test_data = products.random_split(.8, seed=0)
selected_words_model = graphlab.logistic_classifier.create(train_data,
                                                     target='sentiment',
                                        features=[word + '_count' for word in selected_words],
                                                     validation_set=test_data)

PROGRESS: Logistic regression:
PROGRESS: --------------------------------------------------------
PROGRESS: Number of examples          : 133448
PROGRESS: Number of classes           : 2
PROGRESS: Number of feature columns   : 11
PROGRESS: Number of unpacked features : 11
PROGRESS: Number of coefficients    : 12
PROGRESS: Starting Newton Method
PROGRESS: --------------------------------------------------------
PROGRESS: +-----------+----------+--------------+-------------------+---------------------+
PROGRESS: | Iteration | Passes   | Elapsed Time | Training-accuracy | Validation-accuracy |
PROGRESS: +-----------+----------+--------------+-------------------+---------------------+
PROGRESS: | 1         | 2        | 0.114563     | 0.844299          | 0.842842            |
PROGRESS: | 2         | 3        | 0.174291     | 0.844186          | 0.842842            |
PROGRESS: | 3         | 4        | 0.236552     | 0.844276          | 0.843142            |
PROGRESS: | 4         | 5        |

In [84]:
selected_words_model['coefficients'].print_rows(num_rows = 12)

+-----------------+-------+-------+------------------+
|       name      | index | class |      value       |
+-----------------+-------+-------+------------------+
|   (intercept)   |  None |   1   |  1.36728315229   |
|  awesome_count  |  None |   1   |  1.05800888878   |
|   great_count   |  None |   1   |  0.883937894898  |
| fantastic_count |  None |   1   |  0.891303090304  |
|  amazing_count  |  None |   1   |  0.892802422508  |
|    love_count   |  None |   1   |  1.39989834302   |
|  horrible_count |  None |   1   |  -1.99651800559  |
|    bad_count    |  None |   1   | -0.985827369929  |
|  terrible_count |  None |   1   |  -2.09049998487  |
|   awful_count   |  None |   1   |  -1.76469955631  |
|    wow_count    |  None |   1   | -0.0541450123333 |
|    hate_count   |  None |   1   |  -1.40916406276  |
+-----------------+-------+-------+------------------+
[12 rows x 4 columns]



In [64]:
sentiment_model.evaluate(test_data, metric='roc_curve')

{'roc_curve': Columns:
 	threshold	float
 	fpr	float
 	tpr	float
 	p	int
 	n	int
 
 Rows: 100001
 
 Data:
 +-----------+----------------+----------------+-------+------+
 | threshold |      fpr       |      tpr       |   p   |  n   |
 +-----------+----------------+----------------+-------+------+
 |    0.0    |      1.0       |      1.0       | 27976 | 5328 |
 |   1e-05   | 0.909346846847 | 0.998856162425 | 27976 | 5328 |
 |   2e-05   | 0.896021021021 | 0.998748927652 | 27976 | 5328 |
 |   3e-05   | 0.886448948949 | 0.998462968259 | 27976 | 5328 |
 |   4e-05   | 0.879692192192 | 0.998284243637 | 27976 | 5328 |
 |   5e-05   | 0.875187687688 | 0.998212753789 | 27976 | 5328 |
 |   6e-05   | 0.872184684685 | 0.998177008865 | 27976 | 5328 |
 |   7e-05   | 0.868618618619 | 0.998034029168 | 27976 | 5328 |
 |   8e-05   | 0.864677177177 | 0.997998284244 | 27976 | 5328 |
 |   9e-05   | 0.860735735736 | 0.997962539319 | 27976 | 5328 |
 +-----------+----------------+----------------+-------+------

In [65]:
selected_words_model.evaluate(test_data, metric='roc_curve')

{'roc_curve': Columns:
 	threshold	float
 	fpr	float
 	tpr	float
 	p	int
 	n	int
 
 Rows: 100001
 
 Data:
 +-----------+-----+-----+-------+------+
 | threshold | fpr | tpr |   p   |  n   |
 +-----------+-----+-----+-------+------+
 |    0.0    | 1.0 | 1.0 | 27976 | 5328 |
 |   1e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   2e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   3e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   4e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   5e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   6e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   7e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   8e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   9e-05   | 1.0 | 1.0 | 27976 | 5328 |
 +-----------+-----+-----+-------+------+
 [100001 rows x 5 columns]
 Note: Only the head of the SFrame is printed.
 You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.}

In [66]:
sentiment_model.show(view='Evaluation')

In [68]:
selected_words_model.show(view='Evaluation')

In [85]:
test_data.show()

## Analyze Baby Trend Diaper Champ Reviews

In [69]:
diaper_champ_reviews = products[products['name'] == 'Baby Trend Diaper Champ']

In [70]:
diaper_champ_reviews.show()

In [72]:
print diaper_champ_reviews.column_names()

['name', 'review', 'rating', 'word_count', 'sentiment', 'awesome_count', 'great_count', 'fantastic_count', 'amazing_count', 'love_count', 'horrible_count', 'bad_count', 'terrible_count', 'awful_count', 'wow_count', 'hate_count']


In [79]:
diaper_champ_reviews['sentiment_predict_words_all'] = sentiment_model.predict(diaper_champ_reviews, 
                                                                              output_type = 'probability')
diaper_champ_reviews['sentiment_predict_words_sld'] = selected_words_model.predict(diaper_champ_reviews, 
                                                                              output_type = 'probability')

In [80]:
diaper_champ_reviews[['sentiment', 'sentiment_predict_words_all', 'sentiment_predict_words_sld']].show()

In [81]:
print diaper_champ_reviews.sort('sentiment_predict_words_sld')[-1]

{'awesome_count': 0, 'rating': 4.0, 'sentiment_predict_words_sld': 0.9984234145936198, 'name': 'Baby Trend Diaper Champ', 'sentiment': 1, 'amazing_count': 0, 'horrible_count': 0, 'review': 'I LOVE LOVE LOVE this product! It is SO much easier to use than the Diaper Genie, (you need a PHD in poopy to figure out how to use the darn thing!) and it even takes the same bags as my kitchen trash can, shich is super convenient, and cost efficient as I can buy them in bulk.The only reason for not rating it a 5 star was that I did have one small problem with it. The foam gasket in the barrell which keeps the poopy smell inside the unit ripped somehow, and it got VERY stinky. HOWEVER, I contacted the manufacturer though their website, and received an email back the same day stating that this was unusual, and that replacement gaskets were on their way to me. They arrived inside of a week and after replacing, it works great again! (They even sent me extras should it happen again)I HIGHLY reccomend t

In [82]:
print diaper_champ_reviews.sort('sentiment_predict_words_all')[-1]

{'awesome_count': 0, 'rating': 5.0, 'sentiment_predict_words_sld': 0.7969408512906713, 'name': 'Baby Trend Diaper Champ', 'sentiment': 1, 'amazing_count': 0, 'horrible_count': 0, 'review': 'Baby Luke can turn a clean diaper to a dirty diaper in 3 seconds flat. The diaper champ turns the smelly diaper into "what diaper smell" in less time than that. I hesitated and wondered what I REALLY needed for the nursery. This is one of the best purchases we made. The champ, the baby bjorn, fluerville diaper bag, and graco pack and play bassinet all vie for the best baby purchase.Great product, easy to use, economical, effective, absolutly fabulous.UpdateI knew that I loved the champ, and useing the diaper genie at a friend\'s house REALLY reinforced that!! There is no comparison, the chanp is easy and smell free, the genie was difficult to use one handed (which is absolutly vital if you have a little one on a changing pad) and there was a deffinite odor eminating from the genieplus we found that 

## End Experiment